In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from subprocess import check_output
%matplotlib inline
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

import os
import gc
import json
import pickle
import glob

import re
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from bs4 import BeautifulSoup

import tensorflow as tf

import warnings
warnings.filterwarnings("ignore")
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from subprocess import check_output
%matplotlib inline
import os
import gc

import re
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from bs4 import BeautifulSoup
import re
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from bs4 import BeautifulSoup
from fuzzywuzzy import fuzz
from sklearn.manifold import TSNE

from os import path
from PIL import Image

In [2]:
glove_path = 'E:\All Video\MLDL\glove'

In [3]:
def load_txt(name):
    with open(name, "r") as f:
        return f.read()

def load_pickle(name):
    with open(name, "rb") as handle:
        return pickle.load(handle)
    
def dump_pickle(name, file):
    with open(name, "wb") as handle:
        pickle.dump(file, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [4]:
drug_train_data = pd.read_csv("drug_preprocess.csv", index_col="Unnamed: 0")
drug_train_data.head(2)

patient_id name_of_drug use_case_for_drug  \
10091      223808  Depakote ER          Epilepsy   
1009        35602      Anexsia              Pain   

                                       review_by_patient  \
10091  "After trying 4 different meds this one was th...   
1009   "Worked better than Tylenol w/codeine #3 and C...   

       effectiveness_rating drug_approved_by_UIC  number_of_times_prescribed  \
10091                     8             1-Apr-08                          15   
1009                     10             1-Apr-08                          19   

       base_score  review_len  review_n_words  \
10091    7.633384         370              74   
1009     6.127475          88              14   

                                review_by_patient_filter  \
10091  after trying 4 different meds this one was the...   
1009   worked better than tylenol w codeine  3 and ca...   

                           review_by_patient_unique_word  \
10091  ['one', 'gladly', 'stayed', 'scary', 'well', '...   
1009   ['w', 'tylenol', '3', 'better', 'pain', 'caris...   

       len_review_by_patient_unique_word  
10091                                 35  
1009                                  10

In [5]:
# To get the results in 4 decemal points
SAFE_DIV = 0.0001 

STOP_WORDS = stopwords.words("english")
stopword = set(STOP_WORDS)
stopword.add("said")
stopword.add("br")
stopword.add(" ")
stopword.remove("not")
stopword.remove("no")


def preprocess(x):
    x = str(x).lower()
    x = x.replace(",000,000", "m").replace(",000", "k").replace("′", "'").replace("’", "'")\
                           .replace("won't", "will not").replace("cannot", "can not").replace("can't", "can not")\
                           .replace("n't", " not").replace("what's", "what is").replace("it's", "it is")\
                           .replace("'ve", " have").replace("i'm", "i am").replace("'re", " are")\
                           .replace("he's", "he is").replace("she's", "she is").replace("'s", " own")\
                           .replace("%", " percent ").replace("₹", " rupee ").replace("$", " dollar ")\
                           .replace("€", " euro ").replace("'ll", " will").replace("asap", "as soon as possible")
    x = re.sub(r"([0-9]+)000000", r"\1m", x)
    x = re.sub(r"([0-9]+)000", r"\1k", x)
    
    
    porter = PorterStemmer()
    pattern = re.compile('\W')
    
    if type(x) == type(''):
        x = re.sub(pattern, ' ', x)
    
    
    if type(x) == type(''):
        x = porter.stem(x)
        example1 = BeautifulSoup(x)
        x = example1.get_text()
               
    return x
def combine_name_use_review(a, b, c):
    return preprocess(" ".join([a, b, c])) 
     

In [6]:
drug_train_data["combine_name_use_review"] = drug_train_data.loc[:, ["name_of_drug", "use_case_for_drug", "review_by_patient_filter"]].fillna("").apply(lambda x: combine_name_use_review(x["name_of_drug"], x["use_case_for_drug"], x["review_by_patient_filter"]), axis=1)
drug_train_data.head(2)

patient_id name_of_drug use_case_for_drug  \
10091      223808  Depakote ER          Epilepsy   
1009        35602      Anexsia              Pain   

                                       review_by_patient  \
10091  "After trying 4 different meds this one was th...   
1009   "Worked better than Tylenol w/codeine #3 and C...   

       effectiveness_rating drug_approved_by_UIC  number_of_times_prescribed  \
10091                     8             1-Apr-08                          15   
1009                     10             1-Apr-08                          19   

       base_score  review_len  review_n_words  \
10091    7.633384         370              74   
1009     6.127475          88              14   

                                review_by_patient_filter  \
10091  after trying 4 different meds this one was the...   
1009   worked better than tylenol w codeine  3 and ca...   

                           review_by_patient_unique_word  \
10091  ['one', 'gladly', 'stayed', 'scary', 'well', '...   
1009   ['w', 'tylenol', '3', 'better', 'pain', 'caris...   

       len_review_by_patient_unique_word  \
10091                                 35   
1009                                  10   

                                 combine_name_use_review  
10091  depakote er epilepsy after trying 4 different ...  
1009   anexsia pain worked better than tylenol w code...

In [7]:
all_train_name_use_review = list(drug_train_data["combine_name_use_review"])

In [8]:
def create_vocabulary():       # no use
    vocabulary = set()
    [vocabulary.update(sent.split()) for sent in drug_train_data["combine_name_use_review"].values]
    return vocabulary
vocabulary = create_vocabulary()
print(f"vocabulary contains {len(vocabulary)} words")

vocabulary contains 28094 words


# Step 4: Create vocab of most frequent words

In [9]:
def create_vocab(word_count_threshold = 10):
    word_counts = {}
    nsents = 0
    for sent in all_train_name_use_review:
        nsents += 1
        for w in sent.split(' '):
            word_counts[w] = word_counts.get(w, 0) + 1
    c = 0
    for key, val in word_counts.items():
        if len(key) == 1:
            c += 1
            print(key)
    print(c)
    vocab = [w for w in word_counts if word_counts[w] >= word_count_threshold]
    return vocab, word_counts
vocab, word_counts = create_vocab(50)
print('Vocabulary = %d in our trainig data' % (len(vocab)))    # 10 -> 5607, 7-> 6705, 15-> 4477, 30->2985, 50 -> 

4
i
a
w
3
m
2
5
p
s
t
v
6
1
9
e
g
7
b
d
0
8
l
c
u
h
x
q
n
f
o
r
z
y
k
j
_
і
38
Vocabulary = 3164 in our trainig data


In [10]:
def ixtoword_wordtoix():
    ixtoword = {}
    wordtoix = {}
    ix = 1
    for w in vocab:
        wordtoix[w] = ix
        ixtoword[ix] = w
        ix += 1
    return ixtoword, wordtoix
if 'wordtoix.pkl' in os.listdir("../ix_word"):
    print("load")
    ixtoword = load_pickle('../ix_word/ixtoword.pkl')
    wordtoix = load_pickle('../ix_word/wordtoix.pkl')
else:
    ixtoword, wordtoix = ixtoword_wordtoix()
    dump_pickle('../ix_word/ixtoword.pkl', ixtoword)
    dump_pickle('../ix_word/wordtoix.pkl', wordtoix)
    print("dump")
vocab_size = len(ixtoword) + 1
print('size of vocabulary = %d in our trainig data' % (vocab_size))

load
size of vocabulary = 3167 in our trainig data


# Step 6: Maximum length of caption

In [11]:
# def find_max_len():
#     all_desc = list()
#     for key in .keys():
#         [all_desc.append(d) for d in train_img_capt[key]]
#     max_length = max(len(d.split()) for d in all_desc)
#     return max_length

# max_length = find_max_len()
# print('Description Length: %d' % max_length)

In [12]:
max_length = max(len(d.split()) for d in all_train_name_use_review)
max_length

650

# Step 7: embadding index and matrix

In [13]:
# def create_embadding_index():
#     embeddings_index = {} 
#     f = open(os.path.join(glove_path, 'glove.6B.200d.txt'), encoding="utf-8")
#     for line in f:
#         values = line.split()
#         word = values[0]
#         coefs = np.asarray(values[1:], dtype='float32')
#         embeddings_index[word] = coefs
#     return embeddings_index
# if "embeddings_index.pkl" in os.listdir("../ix_word"):
#     print('load')
#     embeddings_index = load_pickle(os.path.join("../ix_word", "embeddings_index.pkl"))
# else:
#     print("dump")
#     embeddings_index = create_embadding_index()
#     dump_pickle(os.path.join("../ix_word", "embeddings_index.pkl"), embeddings_index)

# print(f"There are {len(embeddings_index)} no of words in glove")

In [14]:
def create_embadding_index():
    embeddings_index = {} 
    f = open(os.path.join(glove_path, 'glove.6B.200d.txt'), encoding="utf-8")
    for line in f:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        embeddings_index[word] = coefs
    return embeddings_index
if "embeddings_index.pickle" in os.listdir(r"D:\computer vision\image_caption"):
    print('load')
    embeddings_index = load_pickle(os.path.join(r"D:\computer vision\image_caption", "embeddings_index.pickle"))
else:
    print("dump")
    embeddings_index = create_embadding_index()
    dump_pickle(os.path.join("../ix_word", "embeddings_index.pkl"), embeddings_index)

print(f"There are {len(embeddings_index)} no of words in glove")

load
There are 400000 no of words in glove


In [15]:
def create_embadding_matrix():
    embedding_dim = 200
    embedding_matrix = np.zeros((vocab_size, embedding_dim))
    for word, i in wordtoix.items():
        embedding_vector = embeddings_index.get(word)
        if embedding_vector is not None:
            embedding_matrix[i] = embedding_vector
        else:
            print(i, word)
    return embedding_matrix
if "embeddings_glove.pkl" in os.listdir("../ix_word"):
    print('load')
    embeddings_glove = load_pickle(os.path.join("../ix_word", "embeddings_glove.pkl"))
else:
    print("dump")
    embeddings_glove = create_embadding_matrix()
    dump_pickle(os.path.join("../ix_word", "embeddings_glove.pkl"), embeddings_glove)

print(f"The shape of glove representation is {embeddings_glove.shape}")

load
The shape of glove representation is (3167, 200)


In [16]:
# Refer: https://huggingface.co/transformers/model_doc/distilbert.html#

from transformers import DistilBertTokenizer, TFDistilBertModel

distil_bert = 'distilbert-base-uncased' # Name of the pretrained models

#DistilBERT 
tokenizer = DistilBertTokenizer.from_pretrained(distil_bert)
model1 = TFDistilBertModel.from_pretrained(distil_bert)

Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_transform', 'vocab_projector', 'activation_13', 'vocab_layer_norm']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


In [17]:
for ele in all_train_name_use_review:
    print(ele)

depakote er epilepsy after trying 4 different meds this one was the first i was able to tolerate for a longer period  the seizures came under control and all was well  unfortunatly my amonia levels  a very rare side effect but one that you need to be aware of  began to rise to scary levels so i had to quit as soon as possible  however if i had not had this issue i would have gladly stayed on the drug  
anexsia pain worked better than tylenol w codeine  3 and carisoprodol   worked great for back pain  
androgel hypogonadism  male i  039 m a 35 year old male and i had no idea that lack of testosterone could have such an effect on the body   while my sex drive was on the low side  that was not the major problem   i had been put on various antidepressants over many years   however  my low testosterone level was the real culprit   i would advise all men who have depression issues to have their testosterone levels checked  
echinacea cold symptoms thank you for balanced information  my mothe

risperdal bipolar disorde i was taking seroquel xr for 5 months and was doing fine   then my insurance switched me to risperdal and i don  039 t like it one bit   it doesn  039 t do anything for me   i  039 m going back to the way i was before the seroquel  
daytrana adhd i am a 22 yr old female  hated the significant side effects of vyvase60mg  hated invuniv  love the patch  allows me to control the medication  i usually take it off about 7 hours after putting it on  this allows me to sleep at night  i can focus at work very well and no significant drop  i realized i can not blow dry my hair  or go tanning with it on or i would get a big burst of medication  sometimes have a hard time sleeping if i don  039 t take it off early  
venlafaxine anxiety and stress i have been taking effexor xr for about 3 years now  while i still suffer panic attacks and suffer symptoms like rapid heart palpitations  poor blood circulation in the fingers  excessive sweating of the hands  and hyperventilati

xanax panic disorde this treatment completely stopped my panic attacks which i thought could never be controlled  just take 1 when you get up to guarantee a peaceful day  i tried all the antidepressants  from depakote to lithium they all had some weird side effect   
loestrin 24 fe birth control i  039 ve been using loestrin for almost 3 years now and i love it  i  039 m petite and about 115  at first i did gain a few pounds  i was really sad but then the fat just went away within a month  then my a cups went to a great b almost c  and i got more junk in the trunk  it really shape me out and i  039 m still thin  my boyfriend loves the change haha  it  039 s been working for me  i would recommend it  
mirena birth control i  039 m 22 years old and i am a mother of a 2 year old  i got the mirena in 8 months ago  when it first got place my ob gyn said it would be a little pinch and it feels like nail clippers pinch my insiders and then it fell out when she was clipping the strings  i want

benzocaine pain peripheral neuropathy   used lanacane on area of leg and several toes during the day for relief over  and above four pain medications i take   in spring of 2012 i developed a low red blood count  5  and needed transfusion   after many tests  including bone biopsy was diagnosed with mds and set  up for procrit   i had 1 injection and started  researching my disease   amp  quickly  discovered info on benzocaine  i stopped using immediately  amp  have had  normal tests since then   i lay no blame on anyone but myself because this  cream is meant for temporary use only and i used it for probably 5 or 6 yrs   thank you for your interest  i am a 74 yr female  
acetaminophen   oxycodone chronic pain i  039 m 51 years old and have been dealing with chronic pain last 20 years  put on mscontin 60mg 3 times day  it  039 s long lasting but pain sill comes through  dr  added 10 325 percocet for break through pain  made my life liveable  give it a 10  
ms contin chronic pain 60mg 2x 

onabotulinumtoxina migraine prevention just got my first set of botox injections yesterday   and the experience was easy and i was definitely pleased my doctor took her time with each injection and before i knew i was done 
levonorgestrel birth control so i just had my daughter 1 25 17 and i got this 6 weeks after having her mind you i was still having some bleeding after having my daughter i had 2 weeks after having her then i had my period then i had spotting and now after having this put in 3 17 17  i have not stopped bleeding it is now going on a full month of constant annoyance and every time you think it finally stops it comes back heavy  i hate this  it is a annoying piece of plastic 
levonorgestrel birth control mirena was highly recommended to me by my doctor  i asked a few friends of mine who were already on mirena and they had nothing but positive reviews of it  i have had heavy painful periods ever since puberty and i was horrible at taking the pills  i eventually went off 

...

phenergan nausea vomiting i tried this medicine a day after i vomited three times and had that nausea feeling and that next day i vomited once in the morning but when i went to the medical centre they gave me the prescription for phenergan  i fell asleep instantly for two hours and a half and woke up refreshed and my stomach did not hurt for the rest of the day and i didn  039 t vomit ever since  it  039 s the best medicine for nausea and vomiting  
duavee hot flashes nothing else i tried for over a year had worked  i hadn  039 t slept for more than a few hours at a time  which was exacerbating moodiness and memory problems  three weeks after starting duavee the hot flashes were completely gone and i was sleeping again  just to be sure the change was the medication  i tried taking a half dose    and the hot flashes stared up again  taking the full dose now for 8 months and feel great  
junel fe 1   20 birth control to everyone worried about taking this because of the awful side effects

levonorgestrel birth control ok so pretty much a few days out of each month i would spot very light  no cramps  for the first 6months  thr first two months i was kind of heavy but it would subside really quickly  after that some months i wouldn  039 t even spot at all  the procedure hurt a little  but that was to be expected  overall i  039 m happy with it  barely any cramps  
lorcaserin weight loss on fourth week  beyond impressed  snacking between meals gone  hugely diminished need desire for food  seem to seek healthier food  biggest surprise is it has eliminated any desire for a nice cold beer  my weakness   past diet experiences used smaller serving approach but almost eat the plate  with belviq using smaller portions but can only eat 1 3 to 1 2  side effects   first day headache was major   so challenging that i would have stopped the medicine if it didn  039 t disappear   it was gone on day 2   feel empowered to finally succeed  goal is to lose 25 percent    down 2 notches on be

nexplanon birth control it  039 s very effective against pregnancy but the side effects have been horrible for me  i got it installed in june 2014 after having my baby  in august i noticed 2 patch  039 s of my hair gone and severely thinned out in the front of my hair  i just thought this was due to postpartum hair loss which typically happens 3 4 months after you have a baby  however it is now january 27th 2015 and the hair loss has continued and now has spread to my entire front head around the edges  also since i have had it  i have had no desire for sex  nothing gets me aroused at all  my sex drive is nonexistent  i am going to get it removed soon because the side effects are unbearable  i am most upset by my hair loss  
citalopram depression i  039 ve been taking 20 mg for 4 days  it  039 s been 4 of the most bizarre days of my life   i take the medicine around 6pm  feel good until i go to sleep  and then wake up with extreme anxiety around 3 am   i then fall back asleep and strug

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




citalopram depression as you get older you take more knocks and psychological blows to your belief system and at 33   had depression all my life didn  039 t really care lived with it long enough and i felt it kept me grounded   i started to lose control of my thinking and my depression became overwhelming  hopelessness and pointlessness in living became a 24 hour battle  i was suicidal and anxiety and constant panic attacks were causing me to lose belief in any sort of future  my dad died because of depression and drug  alcohol misuse  the last thing i wanted was to take medication for it  but it was either go to the doctor or die  8 months on 40mg a day depression is under control and without doubt i  039 m learning to live again thanks to these  
tretinoin photoaging of the skin i heard alot of people trying this for acne  amp  breaking out  so i was apprehensive  i don  039 t have acne anymore   i used to have perioral dermatitus  acne around the mouth  which i got anibiotics for a

In [18]:
def find_vec(sent):
    vec = tokenizer.encode(sent)
    vec = tf.constant(vec)[None, :]
    return model1(vec)[0][0, 0, :].numpy()

# distill_bert_embedding = np.zeros((len(all_train_name_use_review), 768))
def create_embadding_distil():
    global distill_bert_embedding
    embedding_dim = 768
    for i, sent in enumerate(all_train_name_use_review):
        embedding_vector = find_vec(sent[:2000])
        print(i, sent[0:20])
        if embedding_vector is not None:
            distill_bert_embedding[i] = embedding_vector
        else:
            print(i,"NNNNNNNNNNNNNNNNNNNN",  word)
    return distill_bert_embedding

In [19]:
if 'distill_bert_embedding.pkl' in os.listdir("../ix_word"):
    print("load")
    distill_bert_embedding = load_pickle('../ix_word/distill_bert_embedding.pkl')
else:
    distill_bert_embedding = create_embadding_distil()
    dump_pickle('../ix_word/distill_bert_embedding.pkl', distill_bert_embedding)
    print("dump")

load


In [20]:
distill_bert_embedding.shape

(32165, 768)

In [21]:
combine_name_use_review_df = pd.DataFrame(distill_bert_embedding, columns=[f"review_{i}" for i in range(768)])
combine_name_use_review_df.head(2)

review_0  review_1  review_2  review_3  review_4  review_5  review_6  \
0  0.059691  0.008081  0.080178 -0.266999 -0.264136 -0.360968   0.64633   
1 -0.477708 -0.197286 -0.113292 -0.019980 -0.573079 -0.220722   0.34921   

   review_7  review_8  review_9  ...  review_758  review_759  review_760  \
0  0.423532 -0.074173 -0.070809  ...   -0.140880   -0.184657    0.068444   
1 -0.051921 -0.013572 -0.067297  ...    0.134501   -0.330719   -0.052216   

   review_761  review_762  review_763  review_764  review_765  review_766  \
0   -0.305117    0.219165   -0.065599   -0.351725   -0.171581    0.362696   
1    0.190429    0.398500    0.230648   -0.213165   -0.396574    0.421274   

   review_767  
0   -0.022024  
1    0.357504  

[2 rows x 768 columns]

In [22]:
drug_train_data.head(2)

patient_id name_of_drug use_case_for_drug  \
10091      223808  Depakote ER          Epilepsy   
1009        35602      Anexsia              Pain   

                                       review_by_patient  \
10091  "After trying 4 different meds this one was th...   
1009   "Worked better than Tylenol w/codeine #3 and C...   

       effectiveness_rating drug_approved_by_UIC  number_of_times_prescribed  \
10091                     8             1-Apr-08                          15   
1009                     10             1-Apr-08                          19   

       base_score  review_len  review_n_words  \
10091    7.633384         370              74   
1009     6.127475          88              14   

                                review_by_patient_filter  \
10091  after trying 4 different meds this one was the...   
1009   worked better than tylenol w codeine  3 and ca...   

                           review_by_patient_unique_word  \
10091  ['one', 'gladly', 'stayed', 'scary', 'well', '...   
1009   ['w', 'tylenol', '3', 'better', 'pain', 'caris...   

       len_review_by_patient_unique_word  \
10091                                 35   
1009                                  10   

                                 combine_name_use_review  
10091  depakote er epilepsy after trying 4 different ...  
1009   anexsia pain worked better than tylenol w code...

In [23]:
print("Number of features in preprocessed dataframe :", drug_train_data.shape[1])
print("Number of features in nlp dataframe :", combine_name_use_review_df.shape[1])

Number of features in preprocessed dataframe : 14
Number of features in nlp dataframe : 768


In [24]:
# storing the final features to csv file
if not os.path.isfile('../ix_word/final_features.csv'):
    combine_name_use_review_df['patient_id']=drug_train_data['patient_id']
    combine_name_use_review_df['effectiveness_rating']=drug_train_data['effectiveness_rating']
    combine_name_use_review_df['drug_approved_by_UIC']=drug_train_data['drug_approved_by_UIC']
    combine_name_use_review_df['number_of_times_prescribed']=drug_train_data['number_of_times_prescribed']
    combine_name_use_review_df['len_review_by_patient_unique_word']=drug_train_data['len_review_by_patient_unique_word']
    combine_name_use_review_df['base_score']=drug_train_data['base_score']
    first_column = combine_name_use_review_df.pop('patient_id')
    combine_name_use_review_df.insert(0, 'patient_id', first_column)
    combine_name_use_review_df.to_csv('../ix_word/final_features.csv')

In [25]:
combine_name_use_review_df.head(2)

review_0  review_1  review_2  review_3  review_4  review_5  review_6  \
0  0.059691  0.008081  0.080178 -0.266999 -0.264136 -0.360968   0.64633   
1 -0.477708 -0.197286 -0.113292 -0.019980 -0.573079 -0.220722   0.34921   

   review_7  review_8  review_9  ...  review_758  review_759  review_760  \
0  0.423532 -0.074173 -0.070809  ...   -0.140880   -0.184657    0.068444   
1 -0.051921 -0.013572 -0.067297  ...    0.134501   -0.330719   -0.052216   

   review_761  review_762  review_763  review_764  review_765  review_766  \
0   -0.305117    0.219165   -0.065599   -0.351725   -0.171581    0.362696   
1    0.190429    0.398500    0.230648   -0.213165   -0.396574    0.421274   

   review_767  
0   -0.022024  
1    0.357504  

[2 rows x 768 columns]

In [26]:
combine_name_use_review_df.shape

(32165, 768)

## Test Data

In [27]:
drug_test_data = pd.read_csv("drug_test_preprocess.csv", index_col="Unnamed: 0")
drug_test_data.head(2)

patient_id name_of_drug                                  review_by_patient  \
0      163740  Mirtazapine  "I&#039;ve tried a few antidepressants over th...   
1       39293     Contrave  "Contrave combines drugs that were used for al...   

  drug_approved_by_UIC  number_of_times_prescribed use_case_for_drug  \
0            28-Feb-12                          22        Depression   
1             5-Mar-17                          35       Weight Loss   

   effectiveness_rating                           review_by_patient_filter  \
0                    10  i  039 ve tried a few antidepressants over the...   
1                     9  contrave combines drugs that were used for alc...   

                       review_by_patient_unique_word  \
0  ['insomnia', 'changed', 'tried', 'actually', '...   
1  ['work', 'want', 'contrave', 'know', 'obesity'...   

   len_review_by_patient_unique_word  review_len  review_n_words  
0                                 36         439              68  
1                                 62         782             143

In [28]:
drug_test_data["combine_name_use_review"] = drug_test_data.loc[:, ["name_of_drug", "use_case_for_drug", "review_by_patient_filter"]].fillna("").apply(lambda x: combine_name_use_review(x["name_of_drug"], x["use_case_for_drug"], x["review_by_patient_filter"]), axis=1)
drug_test_data.head(2)

patient_id name_of_drug                                  review_by_patient  \
0      163740  Mirtazapine  "I&#039;ve tried a few antidepressants over th...   
1       39293     Contrave  "Contrave combines drugs that were used for al...   

  drug_approved_by_UIC  number_of_times_prescribed use_case_for_drug  \
0            28-Feb-12                          22        Depression   
1             5-Mar-17                          35       Weight Loss   

   effectiveness_rating                           review_by_patient_filter  \
0                    10  i  039 ve tried a few antidepressants over the...   
1                     9  contrave combines drugs that were used for alc...   

                       review_by_patient_unique_word  \
0  ['insomnia', 'changed', 'tried', 'actually', '...   
1  ['work', 'want', 'contrave', 'know', 'obesity'...   

   len_review_by_patient_unique_word  review_len  review_n_words  \
0                                 36         439              68   
1                                 62         782             143   

                             combine_name_use_review  
0  mirtazapine depression i  039 ve tried a few a...  
1  contrave weight loss contrave combines drugs t...

In [29]:
all_test_name_use_review = list(drug_test_data["combine_name_use_review"])
len(all_test_name_use_review)

10760

In [30]:
def find_vec(sent):
    vec = tokenizer.encode(sent)
    vec = tf.constant(vec)[None, :]
    return model1(vec)[0][0, 0, :].numpy()

distill_bert_embedding_test = np.zeros((len(all_test_name_use_review), 768))
def create_embadding_distil():
    global distill_bert_embedding_test
    embedding_dim = 768
    for i, sent in enumerate(all_test_name_use_review):
        embedding_vector = find_vec(sent[:2000])
        print(i, sent[0:20])
        if embedding_vector is not None:
            distill_bert_embedding[i] = embedding_vector
        else:
            print(i,"NNNNNNNNNNNNNNNNNNNN",  word)
    return distill_bert_embedding

In [31]:
if 'distill_bert_embedding_test.pkl' in os.listdir("../ix_word"):
    print("load")
    distill_bert_embedding_test = load_pickle('../ix_word/distill_bert_embedding_test.pkl')
else:
    distill_bert_embedding_test = create_embadding_distil()
    dump_pickle('../ix_word/distill_bert_embedding_test.pkl', distill_bert_embedding_test)
    print("dump")

0 mirtazapine depressi
1 contrave weight loss
2 zyclara keratosis 4 
3 methadone opiate wit
4 ambien insomnia ditt
5 nuvigil narcolepsy a
6 blisovi fe 1   20 bi
7 ivermectin rosacea i
8 nuvaring birth contr
9 escitalopram depress
10 gabapentin bipolar d
11 aubra birth control 
12 ethinyl estradiol   
13 miconazole vaginal y
14 nitrofurantoin bladd
15 tamsulosin benign pr
16 cryselle endometrios
17 pramipexole restless
18 nifedipine raynaud o
19 sertraline major dep
20 phentermine obesity 
21 campral alcohol depe
22 buspar anxiety i did
23 promethazine nausea 
24 tioconazole vaginal 
25 levonorgestrel birth
26 nicoderm cq smoking 
27 fluoxetine major dep
28 depakote bipolar dis
29 lo loestrin fe birth
30 phentermine weight l
31 amitriptyline ibromy
32 beyaz acne i have be
33 levonorgestrel emerg
34 zoloft social anxiet
35 desvenlafaxine depre
36 pristiq major depres
37 depo provera birth c
38 sovaldi hepatitis c 
39 valacyclovir cold so
40 quetiapine bipolar d
41 estradiol postmenopa
42

333 suboxone opiate depe
334 invokana diabetes  t
335 risperidone paranoid
336 levonorgestrel birth
337 trintellix depressio
338 etonogestrel birth c
339 natalizumab multiple
340 tylenol with codeine
341 prozac anxiety and s
342 acetaminophen   hydr
343 prednisone sinusitis
344 venlafaxine depressi
345 azithromycin chlamyd
346 magnesium sulfate   
347 azelastine allergic 
348 duloxetine depressio
349 efinaconazole onycho
350 pradaxa prevention o
351 etonogestrel birth c
352 sanctura overactive 
353 lorazepam anxiety af
354 benadryl allergy urt
355 trintellix depressio
356 phentermine weight l
357 lutera birth control
358 phentermine weight l
359 ambien insomnia i  0
360 trintellix major dep
361 venlafaxine anxiety 
362 ocella birth control
363 etonogestrel birth c
364 lasix edema have onl
365 amoxicillin   clavul
366 saxenda obesity i st
367 microgestin fe 1   2
368 viibryd depression t
369 wellbutrin depressio
370 suprep bowel prep ki
371 fluorouracil actinic
372 savella ibromyalgia 


661 ultram er pain this 
662 advair diskus asthma
663 lorcaserin weight lo
664 jalyn benign prostat
665 linzess constipation
666 doxycycline rosacea 
667 methotrexate rheumat
668 acetaminophen   buta
669 lurasidone bipolar d
670 cenestin postmenopau
671 letrozole breast can
672 sprintec birth contr
673 tamsulosin benign pr
674 duloxetine anxiety s
675 desogestrel   ethiny
676 lortab pain lortab i
677 chantix smoking cess
678 amitriptyline migrai
679 levonorgestrel birth
680 sulfasalazine ulcera
681 ethinyl estradiol   
682 levonorgestrel birth
683 fluticasone   salmet
684 dextroamphetamine ad
685 alesse abnormal uter
686 copper birth control
687 levofloxacin sinusit
688 tramadol back pain s
689 atorvastatin high ch
690 vyvanse adhd diagnos
691 strattera adhd worke
692 ortho micronor birth
693 levonorgestrel birth
694 ethinyl estradiol   
695 venlafaxine panic di
696 wellbutrin depressio
697 dapsone acne i  039 
698 desvenlafaxine depre
699 oxytrol overactive b
700 metronidazole bacter


989 etonogestrel birth c
990 temazepam insomnia o
991 sertraline generaliz
992 diphenhydramine inso
993 lexapro generalized 
994 vilazodone depressio
995 citalopram depressio
996 tramadol pain follow
997 topamax bipolar diso
998 fluoxetine anxiety a
999 fetzima major depres
1000 prozac anxiety and s
1001 desogestrel   ethiny
1002 monistat 7 day combi
1003 ethinyl estradiol   
1004 augmentin sinusitis 
1005 vancomycin bacterial
1006 nuvigil narcolepsy i
1007 ortho evra birth con
1008 ethinyl estradiol   
1009 asmanex twisthaler a
1010 alprazolam anxiety o
1011 simply sleep insomni
1012 duloxetine back pain
1013 paroxetine anxiety a
1014 lisinopril high bloo
1015 tussionex pennkineti
1016 methotrexate rheumat
1017 liraglutide diabetes
1018 ambien insomnia i ha
1019 soolantra rosacea so
1020 contrave weight loss
1021 chantix smoking cess
1022 fenofibrate hypertri
1023 adipex p weight loss
1024 minocycline acne i a
1025 vraylar schizophreni
1026 tramadol pain takes 
1027 lurasidone bipolar

1305 terbinafine tinea cr
1306 tretinoin acne i sta
1307 duloxetine anxiety s
1308 zoloft obsessive com
1309 nitrofurantoin urina
1310 lasix 33  span  user
1311 bupropion   naltrexo
1312 advair diskus asthma
1313 zoloft depression it
1314 neurontin periodic l
1315 ethinyl estradiol   
1316 taltz plaque psorias
1317 stalevo parkinson ow
1318 pristiq major depres
1319 interferon beta 1b m
1320 dimenhydrinate motio
1321 doxycycline bacteria
1322 hydroxyzine anxiety 
1323 levonorgestrel abnor
1324 lo loestrin fe birth
1325 nexium gerd i  039 v
1326 seroquel schizophren
1327 mibelas 24 fe birth 
1328 magnesium citrate co
1329 ethinyl estradiol   
1330 ethinyl estradiol   
1331 rosuvastatin high ch
1332 chantix smoking cess
1333 duloxetine anxiety i
1334 adalimumab ankylosin
1335 acetaminophen   oxyc
1336 sertraline generaliz
1337 varenicline smoking 
1338 brexpiprazole schizo
1339 acetaminophen   oxyc
1340 infliximab ulcerativ
1341 bupropion adhd this 
1342 venlafaxine ibromyal
1343 ethinyl

...

9521 amphetamine   dextro
9522 ustekinumab psoriasi
9523 beyaz 6  span  users
9524 asenapine bipolar di
9525 movantik constipatio
9526 tamoxifen breast can
9527 topiramate migraine 
9528 effexor xr anxiety i
9529 levora birth control
9530 exenatide diabetes  
9531 harvoni hepatitis c 
9532 levetiracetam seizur
9533 terbinafine tinea cr
9534 contrave obesity wan
9535 interferon beta 1a m
9536 lessina endometriosi
9537 ethinyl estradiol   
9538 doxepin insomnia my 
9539 pregabalin ibromyalg
9540 implanon birth contr
9541 fluoxetine   olanzap
9542 trazodone insomnia i
9543 pravastatin high cho
9544 zubsolv opiate depen
9545 medroxyprogesterone 
9546 contrave obesity i j
9547 suboxone opiate depe
9548 nortriptyline migrai
9549 nitrofurantoin urina
9550 amphetamine adhd thi
9551 divalproex sodium mi
9552 levonorgestrel abnor
9553 nuvaring birth contr
9554 mononessa birth cont
9555 methocarbamol muscle
9556 adapalene acne i hav
9557 tolterodine urinary 
9558 halcion insomnia i w
9559 levoflo

9837 zyprexa schizophreni
9838 sildenafil erectile 
9839 estradiol postmenopa
9840 hydrochlorothiazide 
9841 metoclopramide migra
9842 niacin high choleste
9843 zomig migraine been 
9844 skyla birth control 
9845 nuvaring birth contr
9846 dextroamphetamine ad
9847 voltaren pain i  039
9848 mirena birth control
9849 escitalopram anxiety
9850 mirena birth control
9851 tioconazole vaginal 
9852 bupropion anxiety to
9853 paregoric diarrhea t
9854 ethinyl estradiol   
9855 ponstel period pain 
9856 kerydin onychomycosi
9857 kadian chronic pain 
9858 seconal insomnia ble
9859 risperidone social a
9860 moviprep bowel prepa
9861 dexlansoprazole gerd
9862 metronidazole bacter
9863 plan b emergency con
9864 vilazodone major dep
9865 xanax panic disorde 
9866 quetiapine generaliz
9867 plan b emergency con
9868 smz tmp ds urinary t
9869 bupropion   naltrexo
9870 alesse birth control
9871 lamictal bipolar dis
9872 bupropion smoking ce
9873 duloxetine ibromyalg
9874 doxylamine   pyridox
9875 trulici

10147 prednisone asthma ev
10148 copper birth control
10149 fluocinonide dermati
10150 tadalafil erectile d
10151 etonogestrel birth c
10152 tramadol restless le
10153 lacosamide seizures 
10154 provigil narcolepsy 
10155 etonogestrel birth c
10156 pregabalin ibromyalg
10157 amlodipine high bloo
10158 methotrexate systemi
10159 desvenlafaxine depre
10160 humira plaque psoria
10161 fentanyl chronic pai
10162 terconazole vaginal 
10163 fluvoxamine anxiety 
10164 nicotine smoking ces
10165 meridia obesity meri
10166 ziprasidone bipolar 
10167 zithromax upper resp
10168 lexapro anxiety have
10169 antabuse alcohol dep
10170 bupropion bipolar di
10171 sertraline major dep
10172 eluxadoline irritabl
10173 sprintec birth contr
10174 contrave obesity i a
10175 suprep bowel prep ki
10176 paroxetine anxiety s
10177 amphetamine   dextro
10178 clonazepam anxiety p
10179 suprep bowel prep ki
10180 polyethylene glycol 
10181 ramipril high blood 
10182 hydrocodone pain i s
10183 pletal intermittent 
1

10451 liraglutide diabetes
10452 strattera adhd my so
10453 daytrana adhd my 9yr
10454 bupropion   naltrexo
10455 amoxicillin bacteria
10456 wellbutrin xl major 
10457 fesoterodine overact
10458 acetaminophen   prop
10459 ziana acne i have ha
10460 sertraline depressio
10461 medroxyprogesterone 
10462 lisdexamfetamine adh
10463 skyla birth control 
10464 depo provera birth c
10465 disulfiram alcohol d
10466 lyrica ibromyalgia i
10467 phentermine weight l
10468 olanzapine bipolar d
10469 citalopram depressio
10470 pregabalin periphera
10471 wellbutrin depressio
10472 etonogestrel birth c
10473 iron polysaccharide 
10474 liraglutide weight l
10475 mirabegron overactiv
10476 synthroid underactiv
10477 levonorgestrel birth
10478 diphenhydramine naus
10479 butrans pain i have 
10480 microgestin fe 1   2
10481 wellbutrin depressio
10482 oxycodone pain i hav
10483 victoza obesity i  0
10484 metaxalone muscle sp
10485 penciclovir cold sor
10486 ethinyl estradiol   
10487 acetazolamide pseudo
1

10755 chantix smoking cess
10756 armodafinil narcolep
10757 tamoxifen breast can
10758 levonorgestrel birth
10759 arthrotec sciatica i
dump


In [32]:
combine_name_use_review_df_test = pd.DataFrame(distill_bert_embedding_test, columns=[f"review_{i}" for i in range(768)])
combine_name_use_review_df_test.head(2)

review_0  review_1  review_2  review_3  review_4  review_5  review_6  \
0 -0.019849  0.173974  0.128156 -0.329652 -0.305466 -0.374780  0.513443   
1  0.079807  0.090857  0.170656 -0.152019 -0.202442 -0.290995  0.381226   

   review_7  review_8  review_9  ...  review_758  review_759  review_760  \
0  0.256115 -0.174848 -0.051410  ...   -0.111515   -0.228544   -0.033203   
1  0.454116 -0.339259 -0.183735  ...   -0.072119   -0.301159   -0.060482   

   review_761  review_762  review_763  review_764  review_765  review_766  \
0   -0.091765    0.380650    0.049244   -0.215225   -0.279196    0.303954   
1   -0.068246    0.254681    0.206014   -0.216410   -0.261225    0.255563   

   review_767  
0    0.058522  
1    0.014028  

[2 rows x 768 columns]

In [33]:
print("Number of features in preprocessed dataframe :", drug_test_data.shape[1])
print("Number of features in nlp dataframe :", combine_name_use_review_df_test.shape[1])

Number of features in preprocessed dataframe : 13
Number of features in nlp dataframe : 768


In [35]:
# storing the final features to csv file
if not os.path.isfile('../ix_word/final_features_test.csv'):
    combine_name_use_review_df_test['patient_id']=drug_test_data['patient_id']
    combine_name_use_review_df['effectiveness_rating']=drug_test_data['effectiveness_rating']
    combine_name_use_review_df['drug_approved_by_UIC']=drug_test_data['drug_approved_by_UIC']
    combine_name_use_review_df_test['number_of_times_prescribed']=drug_test_data['number_of_times_prescribed']
    combine_name_use_review_df_test['len_review_by_patient_unique_word']=drug_test_data['len_review_by_patient_unique_word']
    first_column = combine_name_use_review_df_test.pop('patient_id')
    combine_name_use_review_df_test.insert(0, 'patient_id', first_column)
    combine_name_use_review_df_test.to_csv('../ix_word/final_features_test.csv')